In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np

In [4]:
WORK_DIR = "../../src/results/deepglobe/"
WORK_DIR2 = "../../src/results/deepglobe/CbMLC/"

WORK_DIR = "/home/joking/Downloads/results/deepglobe/lamp/"
WORK_DIR2 = "/home/joking/Downloads/results/deepglobe/resnet_base/"

CSV_LIST = ["train_results.csv", "valid_results.csv", "test_results.csv", "losses.csv"]
models = ["resnet_base"]#, "CbMLC", "lamp", ]


In [18]:
def plot_df(dir, title ="model"):

    # list of model folders with results in it
    # for example 11.07_09.41_.glove_d_300.epochs_50.loss_weighted_bce.sgd.lr_005
    l = [elem for elem in os.listdir(dir) if not elem.startswith('.')]
    n_cols = 3
    n_rows=len(l)
    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*7), dpi=300)

    for i, elem in enumerate(l):
        fig.suptitle(title)
        path=dir+elem+'/results.csv'
        df = pd.read_csv(path)

        axs[i,0].plot(df['epoch'], df['train_maAP']*100, label='train_maAP', linestyle='dotted', c='r')
        axs[i,0].plot(df['epoch'], df['train_miAP']*100, label='train_miAP', linestyle='dotted', c='b')
        axs[i,0].plot(df['epoch'], df['valid_maAP']*100, label='valid_maAP', linestyle='solid', c='r')
        axs[i,0].plot(df['epoch'], df['valid_miAP']*100, label='valid_miAP', linestyle='solid', c='b')

        axs[i,0].set_title(f'{elem}')
        axs[i,0].set_xlabel('epochs')
        axs[i,0].set_ylabel('Metric')
        axs[i,0].grid(axis="x")
        axs[i,0].grid(axis="y")
        axs[i,0].yaxis.set_ticks(np.arange(0,101,10))

        legend = axs[i,0].legend(loc='lower right', shadow=True, fontsize='x-large')


        axs[i,1].plot(df['epoch'], df['train_maF1']*100, label='train_maF1', linestyle='dotted', c='r')
        axs[i,1].plot(df['epoch'], df['train_miF1']*100, label='train_miF1', linestyle='dotted', c='b')
        axs[i,1].plot(df['epoch'], df['valid_maF1']*100, label='valid_maF1', linestyle='solid', c='r')
        axs[i,1].plot(df['epoch'], df['valid_miF1']*100, label='valid_miF1', linestyle='solid', c='b')

        axs[i,1].set_title(f'F1: {elem}')
        axs[i,1].set_xlabel('epochs')
        axs[i,1].set_ylabel('Metrics')
        axs[i,1].grid(axis="x")
        axs[i,1].grid(axis="y")
        axs[i,1].yaxis.set_ticks(np.arange(0,101,10))
        legend = axs[i,1].legend(loc='lower right', shadow=True, fontsize='x-large')

        
        axs[i,2].plot(df['epoch'], df['train_loss']*100, label='train loss', linestyle='dotted', c = 'r')
        axs[i,2].plot(df['epoch'], df['train_loss']*100, label='valid loss', linestyle='solid', c = 'b')
        max_loss = (max(df['train_loss'].max(), df['valid_loss'].max()))

        
        axs[i,2].set_title(f'Loss: {elem}')
        axs[i,2].set_xlabel('epochs')
        axs[i,2].set_ylabel('loss')
        axs[i,1].yaxis.set_ticks(np.arange(0,max_loss+1,max_loss/10))
        axs[i,2].grid(axis="x")
        axs[i,2].grid(axis="y")
        # axs[i,2].yaxis.set_ticks(np.arange(0,101,10)) # doesnt make sense for loss as plots get fucked
        legend = axs[i,2].legend(loc='upper right', shadow=True, fontsize='x-large')
    plt.tight_layout()
    fig.savefig(f"{title}.png", dpi=300)
    #plt.show()

In [19]:
for m in models:
    path = f"/home/joking/Downloads/results/deepglobe/{m}/"
    plot_df(path, title=m)

### Sort directories by noise

In [152]:
import shutil,os
##################### Organize results after noise level ############################
dir_path = "/home/joking/Downloads/cbmlc"
top_dir_list = [elem for elem in os.listdir(dir_path) if not elem.startswith('.')]
for a_dir in top_dir_list:
    an = "addnoise"
    an_idx =  a_dir.find(an)
    new_dir = a_dir[an_idx:]
    new_name = a_dir[:an_idx]
    
    source_dir = os.path.join(dir_path, a_dir)
    
    target_dir = os.path.join(dir_path, new_dir, new_name)
    try:
        os.makedirs(target_dir)
    except OSError as exc:
        pass
    
    
    file_names = os.listdir(source_dir)

    for file_name in file_names:
        shutil.move(os.path.join(source_dir, file_name), target_dir)
    os.rmdir(source_dir)

    

Error: Destination path '/home/joking/Downloads/cbmlc/addnoise_00.subnoise_00/22_07_23_35_.d_300.asl.sgd.lr_001.' already exists

In [156]:
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np


def collect_results(dir_path, model_name=""):
    
    """
    collect results for a model, assumes the runs are already split for noise level ie
    path is: model/addnoise..subnoise.../time ...
    """
    noise_d_list = [elem for elem in os.listdir(dir_path) if not elem.startswith('.')]
    results_list = []
    
    for noise_lvl in noise_d_list:
        model_run_path = os.path.join(dir_path, noise_lvl)
        
        # collect all sub dirs 
        model_run_dirs = [elem for elem in os.listdir(model_run_path) if not elem.startswith('.')]


        for idx, directory in enumerate(model_run_dirs):
            data_list= [model_name]
            index_list = ["Model_Name"]
            # concatenate path
            csv_path = os.path.join(model_run_path, directory, "results.csv")
            tmp_df = pd.read_csv(csv_path, index_col=False)
            
            separate_noise = noise_lvl.split('.')
            for n in separate_noise:
                noise_str,noise_val = n.split('_')
                data_list.append(noise_val)
                index_list.append(noise_str)
                
                
            data_list += directory.split('.')[:-1]
            index_list += ["Time", "dim", 'loss', 'opti', 'lr']

            test_cols= [col for col in tmp_df.columns if col.startswith('test')]
            tmp_df = tmp_df[test_cols]
            last_row = tmp_df.iloc[-1]
            
            final_res= pd.concat([pd.Series(data=data_list, index=index_list)
                                  ,last_row])
            results_list.append(final_res)
        
    df = pd.DataFrame(results_list)
    df.to_csv(f'/home/joking/Downloads/{model_name}_results.csv',  na_rep='NULL', index=False) 
    return df
    
    

In [158]:
model_name = ['resnet']

for m in model_name:
    p =f"/home/joking/Downloads/{m}"
    df = collect_results(p, model_name=m)


In [159]:
df.head(5)

Model_Name addnoise subnoise          Time    dim          loss opti  \
0     resnet       01       00  23_07_05_16_  d_300           asl  sgd   
1     resnet       01       00  23_07_05_16_  d_300           bce  sgd   
2     resnet       01       00  23_07_06_57_  d_300  weighted_bce  sgd   
3     resnet       00       01  23_07_05_59_  d_300           asl  sgd   
4     resnet       00       01  23_07_06_00_  d_300           bce  sgd   

       lr  test_miAP  test_maAP  test_miF1  test_maF1  test_loss  
0  lr_001      0.475      0.449      0.478      0.429     41.578  
1  lr_001      0.809      0.782      0.895      0.852      0.236  
2  lr_001      0.794      0.774      0.873      0.835      0.661  
3  lr_001      0.519      0.485      0.526      0.439     33.576  
4  lr_001      0.788      0.752      0.885      0.844      0.242

In [151]:
losses = ['bce', 'asl', 'weighted_bce']
models = ['lamp', 'cbmlc', 'resnet']
ticks = [0.0, 0.1, 0.3, 0.5, 0.7]

n_cols = len(losses)
n_rows= len(models)

fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*10 ,n_rows*10), dpi=300)
#axs = axs.flatten()

for k, model in enumerate(models):

    model_df = pd.read_csv(f"/home/joking/Downloads/{model}_results.csv")
    model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", 'test_miAP', "test_miF1", "test_maF1", "test_loss"])

    for i, loss in enumerate(losses):
        loss_df = model_df.loc[model_df['loss'] == loss]

        add_noise_df = loss_df.loc[loss_df['subnoise'] == 0]['test_maAP']*100
        sub_noise_df = loss_df.loc[loss_df['addnoise'] == 0]['test_maAP']*100
        mix_noise_df = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_maAP']*100
        
        axs[k,i].plot(ticks, add_noise_df, label='Add', linestyle='solid', c='r')
        axs[k,i].plot(ticks, sub_noise_df, label='Sub', linestyle='solid', c='b')
        axs[k,i].plot(ticks, mix_noise_df, label='Mix Noise', linestyle='solid', c='black')

        axs[k,i].set_title(f'Loss: {loss}')
        axs[k,i].set_xlabel('Noise Level')
        axs[k,i].set_ylabel('macro MAP')
        axs[k,i].grid(axis="x")
        axs[k,i].grid(axis="y")
        axs[k,i].yaxis.set_ticks(np.arange(0,101,10))
        legend = axs[k,i].legend(loc='lower left', shadow=True, fontsize='x-large')
    
plt.show()   

KeyError: 'subnoise'

In [131]:
bce = model_df.loc[model_df['loss'] == 'bce']

add_noise_bce = bce.loc[bce['subnoise'] == 0]['test_maAP']
sub_noise_bce = bce.loc[bce['addnoise'] == 0]['test_maAP']
mix_noise_bce = bce.loc[bce['addnoise'] == bce['subnoise']]['test_maAP']


In [111]:
mix_noise_bce

1     0.781
10    0.737
20    0.640
29    0.424
37    0.118
Name: test_maAP, dtype: float64

In [96]:

fig.suptitle(title)
path=dir+elem+'/results.csv'
df = pd.read_csv(path)

axs[i,0].plot(df['epoch'], df['train_maAP']*100, label='train_maAP', linestyle='dotted', c='r')
axs[i,0].plot(df['epoch'], df['train_miAP']*100, label='train_miAP', linestyle='dotted', c='b')
axs[i,0].plot(df['epoch'], df['valid_maAP']*100, label='valid_maAP', linestyle='solid', c='r')
axs[i,0].plot(df['epoch'], df['valid_miAP']*100, label='valid_miAP', linestyle='solid', c='b')

axs[i,0].set_title(f'{elem}')
axs[i,0].set_xlabel('epochs')
axs[i,0].set_ylabel('Metric')
axs[i,0].grid(axis="x")
axs[i,0].grid(axis="y")
axs[i,0].yaxis.set_ticks(np.arange(0,101,10))

legend = axs[i,0].legend(loc='lower right', shadow=True, fontsize='x-large')


axs[i,1].plot(df['epoch'], df['train_maF1']*100, label='train_maF1', linestyle='dotted', c='r')
axs[i,1].plot(df['epoch'], df['train_miF1']*100, label='train_miF1', linestyle='dotted', c='b')
axs[i,1].plot(df['epoch'], df['valid_maF1']*100, label='valid_maF1', linestyle='solid', c='r')
axs[i,1].plot(df['epoch'], df['valid_miF1']*100, label='valid_miF1', linestyle='solid', c='b')

axs[i,1].set_title(f'F1: {elem}')
axs[i,1].set_xlabel('epochs')
axs[i,1].set_ylabel('Metrics')
axs[i,1].grid(axis="x")
axs[i,1].grid(axis="y")
axs[i,1].yaxis.set_ticks(np.arange(0,101,10))
legend = axs[i,1].legend(loc='lower right', shadow=True, fontsize='x-large')


axs[i,2].plot(df['epoch'], df['train_loss']*100, label='train loss', linestyle='dotted', c = 'r')
axs[i,2].plot(df['epoch'], df['train_loss']*100, label='valid loss', linestyle='solid', c = 'b')
max_loss = (max(df['train_loss'].max(), df['valid_loss'].max()))


axs[i,2].set_title(f'Loss: {elem}')
axs[i,2].set_xlabel('epochs')
axs[i,2].set_ylabel('loss')
axs[i,1].yaxis.set_ticks(np.arange(0,max_loss+1,max_loss/10))
axs[i,2].grid(axis="x")
axs[i,2].grid(axis="y")
# axs[i,2].yaxis.set_ticks(np.arange(0,101,10)) # doesnt make sense for loss as plots get fucked
legend = axs[i,2].legend(loc='upper right', shadow=True, fontsize='x-large')
plt.tight_layout()
fig.savefig(f"{title}.png", dpi=300)

NameError: name 'title' is not defined